In [1]:
import numpy as np  # library to handle data in a vectorized manner

import pandas as pd  # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.options.display.float_format = '{:,.2f}'.format

import requests  # library to handle requests
from pandas.io.json import json_normalize  # tranform JSON file into a pandas dataframe

# import k-means from clustering stage
from sklearn.cluster import KMeans

import geocoder  # import geocoder
import plotly.express as px
import geopandas as gpd # to strore geospatial data
import chart_studio
import chart_studio.plotly as py # for exporting Plotly visualizations to Chart Studio
import plotly.graph_objects as go # to ploty Plotly graph objects
import plotly.io as pio # Plotly renderer
import matplotlib.pyplot as plt # Import Matplotlib for visualizations
import datapane as dp # for exporting map visualizations to Datapane
from plotly.subplots import make_subplots # to make multiple Plotly plots in one instance

import plotly.offline as pyo # Set notebook mode to work in offline
pyo.init_notebook_mode()





from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from pandas.io.json import json_normalize  # tranform JSON file into a pandas dataframe

import folium # map rendering library



# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

print('Libraries imported.')

Libraries imported.


In [2]:
toronto_df = pd.read_excel(
    r'C:\Users\Glenn\Documents\GitHub\Finalproject\finalproject-data\CityofToronto_COVID-19_NeighbourhoodData.xlsx',
    sheet_name='All Cases and Rates by Neighbou') # Dataset with Neighbourhood names and ID
toronto_geo = r'C:\Users\Glenn\Documents\GitHub\Finalproject\finalproject-data\misc\Neighbourhoods.geojson'  # geojson file

print('Datasets downloaded')

Datasets downloaded


In [3]:
toronto_df.dropna(axis=0, inplace=True) # Drop empty rows
toronto_df = toronto_df.astype({"Neighbourhood ID": int}) # Convert Neighbourhood ID to Int type
toronto_df = toronto_df.iloc[:, 0:2] # Slice only relevant columns
toronto_df.head() # Display top 5 rows

Neighbourhood ID        Neighbourhood Name
0               138             Eglinton East
1                47        Don Valley Village
2                38          Lansing-Westgate
3                 9  Edenbridge-Humber Valley
4                44           Flemingdon Park

In [4]:
toronto_gdf = gpd.read_file(toronto_geo) # Read GEOJSON file to a Geopandas dataframe
toronto_gdf.head() # Display initial dataframe to see what outcome is

_id   AREA_ID  AREA_ATTR_ID  PARENT_AREA_ID  AREA_SHORT_CODE  \
0  8261  25886861      25926662           49885               94   
1  8262  25886820      25926663           49885              100   
2  8263  25886834      25926664           49885               97   
3  8264  25886593      25926665           49885               27   
4  8265  25886688      25926666           49885               31   

   AREA_LONG_CODE                     AREA_NAME                     AREA_DESC  \
0              94                 Wychwood (94)                 Wychwood (94)   
1             100          Yonge-Eglinton (100)          Yonge-Eglinton (100)   
2              97           Yonge-St.Clair (97)           Yonge-St.Clair (97)   
3              27  York University Heights (27)  York University Heights (27)   
4              31       Yorkdale-Glen Park (31)       Yorkdale-Glen Park (31)   

      X     Y  LONGITUDE  LATITUDE  OBJECTID   Shape__Area  Shape__Length  \
0  None  None     -79.43     43.68  16491505  3,217,959.61       7,515.78   
1  None  None     -79.40     43.70  16491521  3,160,333.99       7,872.02   
2  None  None     -79.40     43.69  16491537  2,222,464.27       8,130.41   
3  None  None     -79.49     43.77  16491553 25,418,210.12      25,632.34   
4  None  None     -79.46     43.71  16491569 11,566,687.56      13,953.41   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

In [5]:
toronto_gdf = toronto_gdf.iloc[:, 5:]  # Slice dataframe for only relevant attributes
toronto_gdf.rename(columns={'AREA_LONG_CODE': 'Neighbourhood ID'},
                   inplace=True)  # Rename Area_Long_Code as it is same as Neighbourhood ID
toronto_gdf.drop(labels=['AREA_DESC', 'OBJECTID', 'X', 'Y', 'AREA_NAME'],
                 axis=1, inplace=True) # Drop irrelevant columns
toronto_gdf.head() # Display top 5 rows

Neighbourhood ID  LONGITUDE  LATITUDE   Shape__Area  Shape__Length  \
0                94     -79.43     43.68  3,217,959.61       7,515.78   
1               100     -79.40     43.70  3,160,333.99       7,872.02   
2                97     -79.40     43.69  2,222,464.27       8,130.41   
3                27     -79.49     43.77 25,418,210.12      25,632.34   
4                31     -79.46     43.71 11,566,687.56      13,953.41   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

In [6]:
toronto_gdf=toronto_gdf.merge(toronto_df,
                              on='Neighbourhood ID') # Use Merge function for both dataset
cols = toronto_gdf.columns.tolist() # Convert column names to a List
cols = cols[-1:] + cols[:-1] # Move last column to first column
toronto_gdf=toronto_gdf[cols] # Reorder the columns in the Geopandas dataframe
toronto_gdf.head() # Display top 5 rows

Neighbourhood Name  Neighbourhood ID  LONGITUDE  LATITUDE  \
0                 Wychwood                94     -79.43     43.68   
1           Yonge-Eglinton               100     -79.40     43.70   
2           Yonge-St.Clair                97     -79.40     43.69   
3  York University Heights                27     -79.49     43.77   
4       Yorkdale-Glen Park                31     -79.46     43.71   

    Shape__Area  Shape__Length  \
0  3,217,959.61       7,515.78   
1  3,160,333.99       7,872.02   
2  2,222,464.27       8,130.41   
3 25,418,210.12      25,632.34   
4 11,566,687.56      13,953.41   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

In [7]:
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

address = 'Toronto' # name of city we want the location coordinates
geolocator = Nominatim(user_agent="toronto_explorer") # user agent. You can use any name
location = geolocator.geocode(address)
tor_lat = location.latitude # store longitude value
tor_lon = location.longitude # store latitude value

print(tor_lat,tor_lon )

43.6534817 -79.3839347


In [8]:
MAPBOX_ACCESSTOKEN='pk.eyJ1IjoiZ2xlbm4tbWFjYXBpbmxhYyIsImEiOiJja2tlbjRzdm0wMDIyMnBsZHRsc292M2t4In0.fUlpvGK5iBSf6GfdVtLjrw'

In [9]:

# Plotly Express Scatter_Mapbox Initialization
tor_map = px.scatter_mapbox(toronto_gdf, # Geopandas dataframe
                            lat="LATITUDE", # Latitude column in the Geopandas dataframe
                            lon="LONGITUDE", # Longitude column in the Geopandas dataframe
                            hover_name="Neighbourhood Name", # Hover name for the various points
                            hover_data=["Neighbourhood ID"], # Include additional data to hover frame
                            color_discrete_sequence=["blue"], # Colour of data points
                            center={
                                'lat': tor_lat,
                                'lon': tor_lon
                            },
                            zoom=9, # Initial Zoom size of plot
                            height=400,
                            title="Map of Toronto and its 140 Neighbourhoods")
tor_map.update_layout(margin={"r": 0, "t": 30, "l": 0, "b": 0}) # set margins of plot
tor_map.update_layout(mapbox_style="streets",
                      mapbox=dict(bearing=-15, accesstoken=MAPBOX_ACCESSTOKEN))

tor_map.show() # Render map

In [10]:
# Remove the '#' sign below and enter your credentials from Foursquare website
# CLIENT_ID = '   ', CLIENT_SECRET = '  ', LIMIT = '   '

In [11]:
CLIENT_ID = 'VW005C34AHNMGGTRMVQ4PNLCHN2MS2RHK45DYO40XDC35WES' # Foursquare ID
CLIENT_SECRET = 'FKUTIWGMFHRDLE21410RB15WAUQEN3JELAQVFIEYAR2LV04Y' # Foursquare Secret Key
VERSION = '20190425' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

In [12]:
neighborhood_name = toronto_gdf.loc[0, 'Neighbourhood Name']
print(f"The first neighborhood's name is '{neighborhood_name}'.")

The first neighborhood's name is 'Wychwood'.


In [13]:
neighborhood_latitude = toronto_gdf.loc[0, 'LATITUDE'] # neighborhood latitude value
neighborhood_longitude =toronto_gdf.loc[0, 'LONGITUDE'] # neighborhood longitude value

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wychwood are 43.6769192679, -79.425514947.


In [14]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

# get the result to a json file
results = requests.get(url).json()

In [15]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [16]:
venues = results['response']['groups'][0]['items']
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

<ipython-input-16-9de588fd8d99>:2: FutureWarning:

pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead



name      categories   lat    lng
0                  Hillcrest Park            Park 43.68 -79.42
1  Wychwood Barns Farmers' Market  Farmers Market 43.68 -79.42
2                  Wychwood Barns     Event Space 43.68 -79.42
3                  Bob Coffee Bar     Coffee Shop 43.68 -79.42

In [17]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    
    for name, lat, lng in zip(names, latitudes, longitudes):
        # print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
        
    return(nearby_venues)

In [18]:
toronto_gdf = getNearbyVenues(names=toronto_gdf['Neighbourhood Name'],
                                   latitudes=toronto_gdf['LATITUDE'],
                                   longitudes=toronto_gdf['LONGITUDE']
                                  )

In [19]:
toronto_gdf.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0        Wychwood                  43.68                  -79.43   
1        Wychwood                  43.68                  -79.43   
2        Wychwood                  43.68                  -79.43   
3        Wychwood                  43.68                  -79.43   
4  Yonge-Eglinton                  43.70                  -79.40   

                                     Venue  Venue Latitude  Venue Longitude  \
0                           Hillcrest Park           43.68           -79.42   
1           Wychwood Barns Farmers' Market           43.68           -79.42   
2                           Wychwood Barns           43.68           -79.42   
3                           Bob Coffee Bar           43.68           -79.42   
4  North Toronto Memorial Community Centre           43.71           -79.40   

   Venue Category  
0            Park  
1  Farmers Market  
2     Event Space  
3     Coffee Shop  
4             Gym

In [20]:
toronto_gdf.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                 
Agincourt North                                         19   
Agincourt South-Malvern West                            22   
Alderwood                                                5   
Annex                                                   26   
Banbury-Don Mills                                       22   
Bathurst Manor                                           4   
Bay Street Corridor                                     64   
Bayview Village                                          4   
Bayview Woods-Steeles                                    3   
Bedford Park-Nortown                                    25   
Beechborough-Greenbrook                                  2   
Bendale                                                  5   
Birchcliffe-Cliffside                                    4   
Black Creek                                              6   
Blake-Jones                                             15   
Briar Hill-Belgravia                                    13   
Bridle Path-Sunnybrook-York Mills                       10   
Broadview North                                          4   
Brookhaven-Amesbury                                      1   
Cabbagetown-South St. James Town                        47   
Caledonia-Fairbank                                       2   
Casa Loma                                               10   
Centennial Scarborough                                   3   
Church-Yonge Corridor                                  100   
Clairlea-Birchmount                                     11   
Clanton Park                                             4   
Cliffcrest                                               6   
Corso Italia-Davenport                                  21   
Danforth                                                28   
Danforth East York                                       6   
Don Valley Village                                      12   
Dorset Park                                              7   
Dovercourt-Wallace Emerson-Junction                     12   
Downsview-Roding-CFB                                     2   
Dufferin Grove                                          59   
East End-Danforth                                       12   
Edenbridge-Humber Valley                                 3   
Eglinton East                                            5   
Elms-Old Rexdale                                         4   
Englemount-Lawrence                                      6   
Eringate-Centennial-West Deane                           7   
Etobicoke West Mall                                      5   
Flemingdon Park                                         13   
Forest Hill North                                       18   
Forest Hill South                                        2   
Glenfield-Jane Heights                                   5   
Greenwood-Coxwell                                       35   
Guildwood                                                5   
Henry Farm                                               5   
High Park North                                          9   
High Park-Swansea                                       13   
Highland Creek                                           5   
Hillcrest Village                                        3   
Humber Heights-Westmount                                 4   
Humber Summit                                            1   
Humbermede                                               2   
Humewood-Cedarvale                                       5   
Ionview                                                  6   
Islington-City Centre West                              13   
Junction Area                                           54   
Keelesdale-Eglinton West                                 8   
Kennedy Park                                             2   
Kensington-Chinatown                                    49   
Kingsvi

In [21]:
print('There are {} uniques categories.'.format(len(toronto_gdf['Venue Category'].unique())))

There are 285 uniques categories.


In [22]:
# one hot encoding
toronto_gdf_onehot = pd.get_dummies(toronto_gdf[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_gdf_onehot['Neighborhood'] = toronto_gdf['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_gdf_onehot.columns[-1]] + list(toronto_gdf_onehot.columns[:-1])
toronto_gdf_onehot = toronto_gdf_onehot[fixed_columns]

toronto_gdf_onehot.head()

Zoo Exhibit  ATM  Accessories Store  African Restaurant  \
0            0    0                  0                   0   
1            0    0                  0                   0   
2            0    0                  0                   0   
3            0    0                  0                   0   
4            0    0                  0                   0   

   American Restaurant  Amphitheater  Animal Shelter  Antique Shop  \
0                    0             0               0             0   
1                    0             0               0             0   
2                    0             0               0             0   
3                    0             0               0             0   
4                    0             0               0             0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Astrologer  Athletics & Sports  Auto Dealership  \
0                 0           0                   0                0   
1                 0           0                   0                0   
2                 0           0                   0                0   
3                 0           0                   0                0   
4                 0           0                   0                0   

   Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0            0          0           0       0     0    0               0   
1            0          0           0       0     0    0               0   
2            0          0           0       0     0    0               0   
3            0          0           0       0     0    0               0   
4            0          0           0       0     0    0               0   

   Beach  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  Bistro  \
0      0         0           0                   0          0       0   
1      0         0           0                   0          0       0   
2      0         0           0                   0          0       0   
3      0         0           0                   0          0       0   
4      0         0           0                   0          0       0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0              0          0                 0         0              0   
1              0          0                 0         0              0   
2              0          0                 0         0              0   
3              0          0                 0         0              0   
4              0          0                 0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0              0         0   
4                0       0         0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Café  \
0            0         0                 0        0     0

In [23]:
toronto_gdf_grouped = toronto_gdf_onehot.groupby('Neighborhood').mean().reset_index()
toronto_gdf_grouped.head()

Neighborhood  Zoo Exhibit  ATM  Accessories Store  \
0               Agincourt North         0.00 0.00               0.00   
1  Agincourt South-Malvern West         0.00 0.00               0.00   
2                     Alderwood         0.00 0.00               0.00   
3                         Annex         0.00 0.00               0.00   
4             Banbury-Don Mills         0.00 0.00               0.05   

   African Restaurant  American Restaurant  Amphitheater  Animal Shelter  \
0                0.00                 0.00          0.00            0.00   
1                0.00                 0.00          0.00            0.00   
2                0.00                 0.00          0.00            0.00   
3                0.00                 0.00          0.00            0.00   
4                0.00                 0.00          0.00            0.00   

   Antique Shop  Argentinian Restaurant  Art Gallery  Art Museum  \
0          0.00                    0.00         0.00        0.00   
1          0.00                    0.00         0.00        0.00   
2          0.00                    0.00         0.00        0.00   
3          0.00                    0.00         0.00        0.00   
4          0.00                    0.00         0.00        0.00   

   Arts & Crafts Store  Asian Restaurant  Astrologer  Athletics & Sports  \
0                 0.00              0.00        0.00                0.00   
1                 0.00              0.05        0.00                0.00   
2                 0.00              0.00        0.00                0.00   
3                 0.00              0.04        0.00                0.00   
4                 0.00              0.00        0.00                0.00   

   Auto Dealership  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0             0.00         0.00       0.00        0.00    0.05  0.05 0.00   
1             0.00         0.00       0.00        0.00    0.00  0.05 0.00   
2             0.00         0.00       0.00        0.00    0.00  0.00 0.00   
3             0.00         0.00       0.04        0.00    0.00  0.00 0.00   
4             0.00         0.00       0.00        0.00    0.00  0.05 0.00   

   Baseball Field  Beach  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0            0.00   0.00      0.00        0.05                0.00       0.00   
1            0.00   0.00      0.00        0.00                0.00       0.00   
2            0.00   0.00      0.00        0.00                0.00       0.00   
3            0.00   0.00      0.00        0.00                0.00       0.00   
4            0.00   0.00      0.00        0.00                0.00       0.00   

   Bistro  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0    0.00           0.00       0.00              0.00      0.00   
1    0.00           0.00       0.00              0.00      0.00   
2    0.00           0.00       0.00              0.00      0.00   
3    0.00           0.00       0.00              0.00      0.00   
4    0.00           0.00       0.00              0.00      0.00   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0           0.00                  0.00            0.00     0.00         0.00   
1           0.00                  0.00            0.00     0.00         0.00   
2           0.00                  0.00            0.00     0.00         0.00   
3           0.00                  0.00            0.00     0.00         0.00   
4           0.00                  0.00            0.00     0.00         0.00   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0             0.00    0.00      0.00          0.00           0.00      0.00   
1             0.00    0.00      0.00          0.00           0.00      0.00   
2             0.00    0.00      0.00          0.00           0.00      0.00   
3             0.00    0.00      0.00          0.04           0.00      0.00   
4             0.05    0.00      0.

In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_gdf_grouped['Neighborhood']

for ind in np.arange(toronto_gdf_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_gdf_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0               Agincourt North    Chinese Restaurant           Pizza Place   
1  Agincourt South-Malvern West    Chinese Restaurant         Shopping Mall   
2                     Alderwood           Pizza Place           Coffee Shop   
3                         Annex                  Park                  Café   
4             Banbury-Don Mills           Coffee Shop           Pizza Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0   Japanese Restaurant   Fried Chicken Joint    Frozen Yogurt Shop   
1             Pool Hall          Intersection            Restaurant   
2     Convenience Store          Dance Studio         Moving Target   
3        Sandwich Place                   Pub           Shoe Repair   
4          Gourmet Shop                  Bank         Shopping Mall   

  6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0  Fast Food Restaurant           Sandwich Place          Liquor Store   
1          Noodle House     Cantonese Restaurant    Seafood Restaurant   
2          Night Market  New American Restaurant            Nail Salon   
3          Liquor Store        French Restaurant          Burger Joint   
4       Bubble Tea Shop               Shoe Store        Medical Center   

  9th Most Common Venue     10th Most Common Venue  
0            Beer Store                       Bank  
1   Filipino Restaurant            Motorcycle Shop  
2           Music Venue                Music Store  
3           Social Club  Middle Eastern Restaurant  
4  Cantonese Restaurant             Sandwich Place

In [25]:
# set number of clusters
kclusters = 5

toronto_gdf_grouped_clustering = toronto_gdf_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_gdf_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 0, 1, 1, 0, 1])

In [26]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_gdf_merged = toronto_gdf

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_gdf_merged = toronto_gdf_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_gdf_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0        Wychwood                  43.68                  -79.43   
1        Wychwood                  43.68                  -79.43   
2        Wychwood                  43.68                  -79.43   
3        Wychwood                  43.68                  -79.43   
4  Yonge-Eglinton                  43.70                  -79.40   

                                     Venue  Venue Latitude  Venue Longitude  \
0                           Hillcrest Park           43.68           -79.42   
1           Wychwood Barns Farmers' Market           43.68           -79.42   
2                           Wychwood Barns           43.68           -79.42   
3                           Bob Coffee Bar           43.68           -79.42   
4  North Toronto Memorial Community Centre           43.71           -79.40   

   Venue Category  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0            Park               0           Coffee Shop           Event Space   
1  Farmers Market               0           Coffee Shop           Event Space   
2     Event Space               0           Coffee Shop           Event Space   
3     Coffee Shop               0           Coffee Shop           Event Space   
4             Gym               1           Coffee Shop  Fast Food Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Farmers Market                  Park           Zoo Exhibit   
1        Farmers Market                  Park           Zoo Exhibit   
2        Farmers Market                  Park           Zoo Exhibit   
3        Farmers Market                  Park           Zoo Exhibit   
4            Restaurant                   Gym  Caribbean Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  New American Restaurant            Nail Salon           Music Venue   
1  New American Restaurant            Nail Salon           Music Venue   
2  New American Restaurant            Nail Salon           Music Venue   
3  New American Restaurant            Nail Salon           Music Venue   
4              Supermarket        Breakfast Spot           Gas Station   

  9th Most Common Venue 10th Most Common Venue  
0           Music Store                 Museum  
1           Music Store                 Museum  
2           Music Store                 Museum  
3           Music Store                 Museum  
4                Buffet           Burger Joint

In [28]:
# create map
latitude = 43.6532
longitude = -79.3832
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(
        toronto_gdf_merged['Neighborhood Latitude'], 
        toronto_gdf_merged['Neighborhood Longitude'], 
        toronto_gdf_merged['Neighborhood'], 
        toronto_gdf_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [29]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 0, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude  \
0                     43.68           -79.42   
1                     43.68           -79.42   
2                     43.68           -79.42   
3                     43.68           -79.42   
122                   43.66           -79.50   
123                   43.66           -79.49   
124                   43.66           -79.50   
125                   43.75           -79.42   
273                   43.82           -79.27   
274                   43.82           -79.28   
332                   43.75           -79.59   
333                   43.75           -79.58   
466                   43.67           -79.35   
467                   43.67           -79.35   
468                   43.67           -79.35   
469                   43.67           -79.36   
470                   43.67           -79.36   
471                   43.67           -79.35   
559                   43.76           -79.33   
560                   43.76           -79.33   
704                   43.68           -79.38   
705                   43.68           -79.38   
706                   43.68           -79.37   
707                   43.68           -79.38   
839                   43.69           -79.30   
840                   43.69           -79.30   
841                   43.69           -79.30   
842                   43.69           -79.30   
1006                  43.77           -79.18   
1007                  43.77           -79.17   
1008                  43.77           -79.18   
1009                  43.77           -79.18   
1010                  43.77           -79.18   
1023                  43.78           -79.45   
1024                  43.78           -79.45   
1067                  43.77           -79.42   
1068                  43.77           -79.42   
1079                  43.69           -79.31   
1080                  43.69           -79.31   
1081                  43.69           -79.32   
1082                  43.69           -79.31   
1083                  43.69           -79.32   
1084                  43.69           -79.31   
1085                  43.69           -79.32   
1086                  43.69           -79.32   
1087                  43.69           -79.32   
1182                  43.76           -79.46   
1183                  43.76           -79.46   
1184                  43.76           -79.46   
1185                  43.76           -79.46   
1254                  43.80           -79.38   
1255                  43.80           -79.39   
1256                  43.80           -79.39   
1284                  43.76           -79.25   
1285                  43.76           -79.26   
1286                  43.76           -79.26   
1287                  43.76           -79.26   
1288                  43.76           -79.25   
1341                  43.70           -79.48   
1389                  43.69           -79.46   
1390                  43.69           -79.46   
1401                  43.78           -79.16   
1402                  43.78           -79.15   
1403                  43.78           -79.16   
1515                  43.74           -79.45   
1516                  43.74           -79.45   
1517                  43.74           -79.45   
1518                  43.74           -79.45   
1611                  43.73           -79.49   
1612                  43.73           -79.49   
1684                  43.67           -79.53   
1685                  43.67           -79.52   
1686                  43.67           -79.52   
1745                  43.69           -79.41   
1746                  43.69           -79.41   
1747                  43.75           -79.52   
1748                  43.75           -79.51   
1749                  43.75           -79.52   
1750                  43.75           -79.51   
1751                  43.75           -79.51   
1797                  43.66           -79.46   
1798                  43.66           -79.46   
1799                  

In [30]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 1, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude                 Venue Category  \
4                     43.70           -79.40                            Gym   
5                     43.70           -79.41                           Park   
6                     43.70           -79.41                   Burger Joint   
7                     43.70           -79.40            Arts & Crafts Store   
8                     43.70           -79.41            Japanese Restaurant   
9                     43.70           -79.40                 Breakfast Spot   
10                    43.70           -79.40                          Plaza   
11                    43.70           -79.41           Gym / Fitness Center   
12                    43.70           -79.40                  Movie Theater   
13                    43.70           -79.40                     Restaurant   
14                    43.70           -79.41             Persian Restaurant   
15                    43.70           -79.40           Caribbean Restaurant   
16                    43.70           -79.40                   Skating Rink   
17                    43.70           -79.40                    Coffee Shop   
18                    43.70           -79.40                         Bakery   
19                    43.70           -79.40                    Coffee Shop   
20                    43.70           -79.41           Fast Food Restaurant   
21                    43.70           -79.41                    Pizza Place   
22                    43.70           -79.40                    Coffee Shop   
23                    43.70           -79.40                         Buffet   
24                    43.70           -79.41                     Restaurant   
25                    43.70           -79.40             Italian Restaurant   
26                    43.70           -79.40                    Coffee Shop   
27                    43.70           -79.40                 Sandwich Place   
28                    43.70           -79.40                    Salad Place   
29                    43.70           -79.40                            Gym   
30                    43.70           -79.40                           Bank   
31                    43.70           -79.40                     Restaurant   
32                    43.70           -79.40                  Poutine Place   
33                    43.70           -79.41                    Gas Station   
34                    43.70           -79.40           Fast Food Restaurant   
35                    43.70           -79.41                  Deli / Bodega   
36                    43.70           -79.40           Fast Food Restaurant   
37                    43.70           -79.40                    Coffee Shop   
38                    43.70           -79.41                   Liquor Store   
39                    43.70           -79.40                    Supermarket   
40                    43.70           -79.41                            Pub   
41                    43.70           -79.40               Department Store   
42                    43.70           -79.40                  Shopping Mall   
43                    43.70           -79.40                      Juice Bar   
44                    43.69           -79.40                    Supermarket   
45                    43.69           -79.40                     Restaurant   
46                    43.69           -79.39                     Bagel Shop   
47                    43.69           -79.40                   Liquor Store   
48                    43.69           -79.40               Sushi Restaurant   
49                    43.69           -79.39            American Restaurant   
50                    43.69           -79.39                   Chiropractor   
51                    43.69           -79.39                    Yoga Studio   
52                    43.69           -79.39                           Café   
53                    43.69           -79.39            

In [32]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 2, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude              Venue Category  \
632                   43.67           -79.55  Construction & Landscaping   
633                   43.67           -79.54                  Playground   
634                   43.67           -79.55  Construction & Landscaping   
1692                  43.72           -79.55            Business Service   
1693                  43.72           -79.55  Construction & Landscaping   
1694                  43.72           -79.55  Construction & Landscaping   
1695                  43.72           -79.55          African Restaurant   

      Cluster Labels       1st Most Common Venue 2nd Most Common Venue  \
632                2  Construction & Landscaping            Playground   
633                2  Construction & Landscaping            Playground   
634                2  Construction & Landscaping            Playground   
1692               2  Construction & Landscaping      Business Service   
1693               2  Construction & Landscaping      Business Service   
1694               2  Construction & Landscaping      Business Service   
1695               2  Construction & Landscaping      Business Service   

     3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
632          Moving Target          Night Market  New American Restaurant   
633          Moving Target          Night Market  New American Restaurant   
634          Moving Target          Night Market  New American Restaurant   
1692    African Restaurant          Night Market  New American Restaurant   
1693    African Restaurant          Night Market  New American Restaurant   
1694    African Restaurant          Night Market  New American Restaurant   
1695    African Restaurant          Night Market  New American Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
632             Nail Salon           Music Venue           Music Store   
633             Nail Salon           Music Venue           Music Store   
634             Nail Salon           Music Venue           Music Store   
1692            Nail Salon           Music Venue           Music Store   
1693            Nail Salon           Music Venue           Music Store   
1694            Nail Salon           Music Venue           Music Store   
1695            Nail Salon           Music Venue           Music Store   

     9th Most Common Venue 10th Most Common Venue  
632                 Museum          Movie Theater  
633                 Museum          Movie Theater  
634                 Museum          Movie Theater  
1692                Museum          Moving Target  
1693                Museum          Moving Target  
1694                Museum          Moving Target  
1695                Museum          Moving Target

In [33]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 3, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude Venue Category  Cluster Labels  \
1976                  43.65           -79.51           Pool               3   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
1976                  Pool           Zoo Exhibit         Movie Theater   

        4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
1976  New American Restaurant            Nail Salon           Music Venue   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
1976           Music Store                Museum         Moving Target   

     10th Most Common Venue  
1976        Motorcycle Shop

In [34]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 4, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude Venue Category  Cluster Labels  \
1831                  43.76           -79.55     Print Shop               4   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
1831            Print Shop           Zoo Exhibit         Movie Theater   

        4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
1831  New American Restaurant            Nail Salon           Music Venue   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
1831           Music Store                Museum         Moving Target   

     10th Most Common Venue  
1831        Motorcycle Shop

In [35]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 5, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood Latitude, Venue Longitude, Venue Category, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue]
Index: []

In [ ]:
toronto_gdf_merged.loc[toronto_gdf_merged['Cluster Labels'] == 6, toronto_gdf_merged.columns[[1] + list(range(5, toronto_gdf_merged.shape[1]))]]